# gpCAM Test Notebook
In this notebook we will go through many features of gpCAM. Work through it 
and you are ready for your own autonomous experiment. 

## This first cell has nothing to do with gpCAM, it's just a function to plot some results later

In [1]:
import plotly.graph_objects as go
import numpy as np
def plot(x,y,z,data = None):
    fig = go.Figure()
    fig.add_trace(go.Surface(x = x, y = y,z=z))
    if data is not None: 
        fig.add_trace(go.Scatter3d(x=data[:,0], y=data[:,1], z=data[:,2],
                                   mode='markers'))

    fig.update_layout(title='Posterior Mean', autosize=True,
                  width=800, height=800,
                  margin=dict(l=65, r=50, b=65, t=90))


    fig.show()

## Here we want to define some points at which we will predict, still has nothing to do with gpCAM 

In [2]:
x_pred = np.zeros((10000,2))
x = np.linspace(0,10,100)
y = np.linspace(0,10,100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.array([x[i,j],y[i,j]])
        counter += 1

## Let's get after it by setting up a Single-Task GP Autonomous Data Acquisition Run

In [3]:
def optional_acq_func(x,obj):
    #this acquisition function makes the autonomous experiment a Bayesian optimization
    a = 3.0 #3.0 for 95 percent confidence interval
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    return mean + a * cov

def optional_cost_function(origin,x,arguments = None):
    #cost pf l1 motion in the input space
    offset = arguments["offset"]
    slope = arguments["slope"]
    d = np.abs(np.subtract(origin,x))
    c = (d * slope) + offset
    n = np.sum(c)
    return n
def optional_cost_update_function(costs, parameters):
    ###defining a cost update function might look tricky but just need a bit
    ###of tenacity. And remember, this is optional, if you have a great guess for your costs you
    ###don't need to update the costs. Also, if you don't account for costs, this funciton is not needed
    from scipy.optimize import differential_evolution as devo
    print("Cost adjustment in progress...")
    print("old cost parameters: ",parameters)
    bounds = np.array([[0.001,10],[0.0001,10]])
    ###remove outliers:
    origins = []
    points = []
    motions = []
    c   = []
    cost_per_motion = []
    for i in range(len(costs)):
        origins.append(costs[i][0])
        points.append(costs[i][1])
        motions.append(abs(costs[i][0] - costs[i][1]))
        c.append(costs[i][2])
        cost_per_motion.append(costs[i][2]/optional_cost_function(costs[i][0],costs[i][1], parameters))
    mean_costs_per_distance = np.mean(np.asarray(cost_per_motion))
    sd = np.std(np.asarray(cost_per_motion))
    for element in cost_per_motion:
        if (
            element >= mean_costs_per_distance - 2.0 * sd
            and element <= mean_costs_per_distance + 2.0 * sd
        ):
            continue
        else:
            motions.pop(cost_per_motion.index(element))
            c.pop(cost_per_motion.index(element))
            origins.pop(cost_per_motion.index(element))
            points.pop(cost_per_motion.index(element))
            cost_per_motion.pop(cost_per_motion.index(element))
    def compute_l1_cost_misfit(params, origins,points, costs):
        parameters = {"offset": params[0], "slope": params[1]}
        sum1 = 0.0
        for idx in range(len(points)):
            sum1 = sum1 + (
                (optional_cost_function(origins[idx],points[idx],parameters) - costs[idx]) ** 2)
        return sum1
    res = devo(compute_l1_cost_misfit, bounds, args = (origins, points,c), tol=1e-6, disp=True, maxiter=300, popsize=20,polish=False)
    arguments = {"offset": res["x"][0],"slope": res["x"][1:]}
    print("New cost parameters: ", arguments)
    return arguments

In [4]:
import time
from gpcam.autonomous_experimenter import AutonomousExperimenterGP

def instrument(data):
    for entry in data:
        entry["value"] = np.sin(np.linalg.norm(entry["position"]))
        entry["cost"]  = [np.array([0,0]),entry["position"],np.sum(entry["position"])]
    return data
#initialization
#feel free to try different acquisition functions, e.g. optional_acq_func, "covariance", "shannon_ig"
#note how costs are defined in for the autonomous experimenter
my_ae = AutonomousExperimenterGP(np.array([[0,10],[0,10]]),instrument,
                                 np.ones((3)),np.array([[0.001,100],[0.001,100],[0.001,100]]),
                                 init_dataset_size= 20, 
                                 acq_func = optional_acq_func, 
                                 #cost_func = optional_cost_function, 
                                 #cost_update_func = optional_cost_update_function,
                                 cost_func_params={"offset": 5.0,"slope":10.0})


print("length of the dataset: ",len(my_ae.x))

#training
#my_ae.train_async() #train asynchronously
my_ae.train()       #or not
#print("Initial training submitted")
#for i in range(2): #this loop shows how hyperparameters are changing if they are trained asynchronously
#    time.sleep(2)


/home/marcus/VirtualEnvironments/gpCAM7/lib/python3.8/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return array(a, dtype, copy=False, order=order)


New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
Costs successfully initialized
##################################################################################
Initialization successfully concluded
now train(...) or train_async(...), and then go(...)
##################################################################################
length of the dataset:  20
fvGP training started with  20  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1. 1.]  with old log likelihood:  21.454008206021626
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  20
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= 21.4175
differential_evolution step 2: f(x)= 20.9198
differential_evolution step 3

## Let's see what our initial model looks like

In [5]:
f = my_ae.gp_optimizer.posterior_mean(x_pred)["f(x)"]
f_re = f.reshape(100,100)

plot(x,y,f_re, data = np.column_stack([my_ae.x,my_ae.y]))

## Let's run the autonomus loop to 100 points

In [6]:
#run the loop
my_ae.go(N = 100, acq_func_opt_setting = lambda number: "global" if number % 1 == 0 else "local",
            training_opt_callable = None,
            training_opt_max_iter = 20,
            training_opt_pop_size = 10,
            training_opt_tol      = 1e-6,
            acq_func_opt_max_iter = 20,
            acq_func_opt_pop_size = 20,
            acq_func_opt_tol      = 1e-6,
            acq_func_opt_tol_adjust = [True,0.1])#,update_cost_func_at = [30])
print("length of the dataset is now: ", len(my_ae.x))
#and that runs the autonomous loop

Date and time:        2021-07-19_15_28_15



iteration:  20
Run Time:  0.0003445148468017578      seconds
Number of measurements:  20
hps:  [0.51765615 2.34198696 2.05716288]
ask() initiated with hyperparameters: [0.51765615 2.34198696 2.05716288]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  1e-06
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -1.72303
differential_evolution step 2: f(x)= -1.72303
differential_evolution step 3: f(x)= -1.72505
differential_evolution step 4: f(x)= -1.72505
differential_evolution step 5: f(x)= -1.72661
differential_evolution step 6: f(x)= -1.72661
differential_evolution step 7: f(x)= -1.72709
differential_evolution step 8: f(x)= -1.72709
differential_evolution step 9: f(x)= -1.72719
differential_evolution step 10: f(x)= -1.7272
differential_evolution 

/home/marcus/VirtualEnvironments/gpCAM7/lib/python3.8/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning:

Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.



differential_evolution step 1: f(x)= -1.52807
acquisition funciton optimization tolerance changed to:  0.15280707273384764
Next points to be requested: 
[[5.82186987 3.82797725]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.48726764 1.66543068 1.38152767]



iteration:  22
Run Time:  0.21340203285217285      seconds
Number of measurements:  22
hps:  [0.48726764 1.66543068 1.38152767]
ask() initiated with hyperparameters: [0.48726764 1.66543068 1.38152767]
optimization method:  global
bounds:  None
finding acquisition funct

differential_evolution step 1: f(x)= -1.45994
differential_evolution step 2: f(x)= -1.46547
acquisition funciton optimization tolerance changed to:  0.14654728573101786
Next points to be requested: 
[[0.02778995 7.65301007]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.48726764 1.66543068 1.38152767]



iteration:  32
Run Time:  0.6244773864746094      seconds
Number of measurements:  32
hps:  [0.48726764 1.66543068 1.38152767]
ask() initiated with hyperparameters: [0.48726764 1.66543068 1.38152767]
optimization method:  g

differential_evolution step 1: f(x)= -1.44451
differential_evolution step 2: f(x)= -1.44451
acquisition funciton optimization tolerance changed to:  0.14445095025155208
Next points to be requested: 
[[5.87824316 5.71957229]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.48726764 1.66543068 1.38152767]



iteration:  38
Run Time:  0.8362407684326172      seconds
Number of measurements:  38
hps:  [0.48726764 1.66543068 1.38152767]
ask() initiated with hyperparameters: [0.48726764 1.66543068 1.38152767]
optimization method:  g

...

differential_evolution step 1: f(x)= -1.06678
differential_evolution step 2: f(x)= -1.06678
differential_evolution step 3: f(x)= -1.06678
differential_evolution step 4: f(x)= -1.06678
differential_evolution step 5: f(x)= -1.06678
acquisition funciton optimization tolerance changed to:  0.10667795217380956
Next points to be requested: 
[[1.00315078 7.86850628]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.75766756 8.19984414 6.915725  ]



iteration:  72
Run Time:  2.9761853218078613      seconds
Number of measurements:  72

differential_evolution step 4: f(x)= -1.05987
differential_evolution step 5: f(x)= -1.05987
acquisition funciton optimization tolerance changed to:  0.10598737585172627
Next points to be requested: 
[[1.53703049 7.83206916]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.75766756 8.19984414 6.915725  ]



iteration:  80
Run Time:  3.5342347621917725      seconds
Number of measurements:  80
hps:  [0.75766756 8.19984414 6.915725  ]
ask() initiated with hyperparameters: [0.75766756 8.19984414 6.915725  ]
optimization method:  g

differential_evolution step 2: f(x)= -1.04129
differential_evolution step 3: f(x)= -1.04129
differential_evolution step 4: f(x)= -1.04129
differential_evolution step 5: f(x)= -1.04129
differential_evolution step 6: f(x)= -1.04129
differential_evolution step 7: f(x)= -1.04129
acquisition funciton optimization tolerance changed to:  0.10412896132973898
Next points to be requested: 
[[6.47502614 4.47093076]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [ 0.93836504 12.65670484 10.62857761]



iteration:  85
Run Time:  3.99500918

differential_evolution step 4: f(x)= -1.03787
differential_evolution step 5: f(x)= -1.03787
acquisition funciton optimization tolerance changed to:  0.10378650910924055
Next points to be requested: 
[[1.77125762 7.71421643]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [ 0.93836504 12.65670484 10.62857761]



iteration:  90
Run Time:  4.36209774017334      seconds
Number of measurements:  90
hps:  [ 0.93836504 12.65670484 10.62857761]
ask() initiated with hyperparameters: [ 0.93836504 12.65670484 10.62857761]
optimization met

differential_evolution step 4: f(x)= -1.03894
differential_evolution step 5: f(x)= -1.03894
acquisition funciton optimization tolerance changed to:  0.10389420756459274
Next points to be requested: 
[[4.8223355  6.05334716]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [ 0.93836504 12.65670484 10.62857761]



iteration:  97
Run Time:  4.989035367965698      seconds
Number of measurements:  97
hps:  [ 0.93836504 12.65670484 10.62857761]
ask() initiated with hyperparameters: [ 0.93836504 12.65670484 10.62857761]
optimization me






## Now let's plot the posterior mean after the experiment has concluded

In [7]:
res = my_ae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f, data = np.column_stack([my_ae.x,my_ae.y]))

## Running a Multi-Task GP Autonomous Data Acquisition
This example uses 21 (!) dim robot data and 7 tasks, which you can all use or pick a subset of them

In [8]:
##prepare some data
import numpy as np
from scipy.interpolate import griddata
data = np.load("sarcos.npy")
print(data.shape)
x = data[:,0:21]
y = data[:,21:23]

(4449, 28)


In [9]:
from gpcam.autonomous_experimenter import AutonomousExperimenterFvGP


def instrument(data):
    for entry in data:
        entry["values"] = griddata(x,y,entry["position"],method = "nearest", fill_value = 0)[0]
        entry["value positions"] = np.array([[0],[1]])
    return data

input_s = np.array([np.array([np.min(x[:,i]),np.max(x[:,i])]) for i in range(len(x[0]))])
print("index set (input space) bounds:")
print(input_s)
print("hps bounds:")
hps_bounds = np.empty((22,2))
hps_bounds[:,0] = 0.0001
hps_bounds[:,1] = 100.0
hps_bounds[0] = np.array([0.0001, 10000])
print(hps_bounds)
print("shape of y: ")
print(y.shape)

my_fvae = AutonomousExperimenterFvGP(input_s,2,1,instrument,np.ones((22)),hps_bounds,
                                     init_dataset_size= 10)
my_fvae.train()
my_fvae.go(N = 100)

index set (input space) bounds:
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
hps bounds:
[[1.e-04 1.e+04]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]]
shape of y: 
(4449, 2)
CAUTION: fvGP reports that you h

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [240.80023103  29.56935377  38.1348407   47.22601957  43.71455975
  81.6163652   32.51821406  18.40116464  76.29516348  63.7612488
  98.06251804  55.5220469   27.12538585  37.27162565  68.72599999
  88.94973131  91.2014557   39.23432991  97.71170987  95.77611687
  90.57577426  49.37726251]



iteration:  12
Run Time:  3.6561310291290283      seconds
Number of measurements:  12
hps:  [240.80023103  29.56935377  38.1348407   47.22601957  43.71455975
  81.6163652   32.51821406  18.40116464  76.29516348  63.7612488
  98.06251804  55.5220469   27.12538585  37.27162565

differential_evolution step 1: f(x)= -13.4294
acquisition funciton optimization tolerance changed to:  1.34294356301722
Next points to be requested: 
[[ -0.26388999  -0.69391708  -0.35154358   1.65046411   0.27909586
   -0.08797095   0.59155699   3.67785693  -1.28681177  -2.2043071
    1.32676703  -0.44274403   1.67321886  -0.11487873  35.85436623
    7.180804   -20.13288412  58.34724271 -31.48956339  13.8802915
   27.34027353]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [240.80023103  29.56935377  38.1348407   47.22601957  43.71455975
  81.6163652   32.51821406  18.40116

differential_evolution step 1: f(x)= -13.2185
acquisition funciton optimization tolerance changed to:  1.32185202171042
Next points to be requested: 
[[-1.01070710e-01 -5.16985327e-01  4.02183059e-02  1.70052398e+00
   4.72741997e-01 -8.00645315e-01  6.77968845e-01 -1.60829376e+00
   1.40316318e+00 -8.80229374e-01  3.70217288e+00 -1.55986494e+00
  -2.07617301e+00 -2.68027574e+00 -4.77214760e+01  1.64236254e+00
  -2.15789578e+01 -2.60061534e+01  2.62787882e+01  1.18124106e+01
  -2.58478143e+01]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
async training is being killed
no training to be killed
    Fresh optimization from scratch via global optimization
fvGP training started with  42  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [240.80023103  29.56935377  38.1348407   47.22601957  43.71455975
 

differential_evolution step 1: f(x)= -12.8055
acquisition funciton optimization tolerance changed to:  1.280551248191074
Next points to be requested: 
[[ -0.3876168   -0.70115207  -0.15278605   0.86285117   0.33981159
    0.08221579  -0.20854201   1.63078844   1.99144703  -0.08910345
    0.76997637  -0.33956883   1.50366692  -1.89066679  -8.72464633
  -24.84870863 -23.01459861  63.73974347 -38.0227083   17.4901826
  -13.75169559]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [240.80267776  29.56949388  38.13484975  47.22604354  43.71458887
  81.61637002  32.51829272  18.401

...

differential_evolution step 1: f(x)= -11.3458
acquisition funciton optimization tolerance changed to:  1.1345834544600046
Next points to be requested: 
[[ -0.19588302  -0.87884143   0.20415461   1.34173488   0.18881278
   -0.36550479  -0.17541225  -1.23397954  -0.65946521   1.99405541
   -3.52968097   1.63901896  -0.06292657  -2.73699348 -44.81541197
  -25.04225536 -23.46031831  53.21152979  18.85227215  16.36024968
   11.00924644]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.4

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.40475766  76.29739117  63.75977654
  98.06257097  55.5204042   27.13719389  37.27275687  68.7271832
  88.59669725  91.13106791  39.62286397  97.79311423  95.7666069
  90.5901165   49.53960207]



iteration:  88
Run Time:  28.16687560081482      seconds
Number of measurements:  88
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.40475766  76.29739117  63.75977654
  98.06257097  55.5204042   27.13719389  37.27275687 

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.40475766  76.29739117  63.75977654
  98.06257097  55.5204042   27.13719389  37.27275687  68.7271832
  88.59669725  91.13106791  39.62286397  97.79311423  95.7666069
  90.5901165   49.53960207]



iteration:  92
Run Time:  30.130637168884277      seconds
Number of measurements:  92
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.40475766  76.29739117  63.75977654
  98.06257097  55.5204042   27.13719389  37.27275687

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.40475766  76.29739117  63.75977654
  98.06257097  55.5204042   27.13719389  37.27275687  68.7271832
  88.59669725  91.13106791  39.62286397  97.79311423  95.7666069
  90.5901165   49.53960207]



iteration:  95
Run Time:  31.977232694625854      seconds
Number of measurements:  95
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.40475766  76.29739117  63.75977654
  98.06257097  55.5204042   27.13719389  37.27275687

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.40475766  76.29739117  63.75977654
  98.06257097  55.5204042   27.13719389  37.27275687  68.7271832
  88.59669725  91.13106791  39.62286397  97.79311423  95.7666069
  90.5901165   49.53960207]



iteration:  98
Run Time:  33.22864031791687      seconds
Number of measurements:  98
hps:  [240.90209044  29.56710388  38.13491383  47.22603343  43.71386624
  81.61638721  32.51725946  18.40475766  76.29739117  63.75977654
  98.06257097  55.5204042   27.13719389  37.27275687 

## Plotting the 0th task in a 2d slice

In [10]:
x_pred = np.zeros((10000,21))
x = np.linspace(input_s[0,0],input_s[0,1],100)
y = np.linspace(input_s[1,0],input_s[1,1],100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.zeros((21))
        x_pred[counter,[0,1]] = np.array([x[i,j],y[i,j]])
        counter += 1
res = my_fvae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f)

## Back to a single task: using the GPOptimizer class directly gives you some more flexibility
We will show more soon!

In [11]:
#/usr/bin/env python
import numpy as np
from gpcam.gp_optimizer import GPOptimizer

#initialize some data
x_data = np.random.uniform(size = (100,1))
y_data = np.sin(x_data)[:,0]


#initialize the GPOptimizer
my_gpo = GPOptimizer(1,np.array([[0,1]]))
#tell() it some data
my_gpo.tell(x_data,y_data)
#initialize a GP ...
my_gpo.init_gp(np.ones(2))
#and train it
my_gpo.train_gp(np.array([[0.001,100],[0.001,100]]))

#let's make a prediction
print(my_gpo.posterior_mean(np.array([0.44])))

#now we can ask for a new point
r = my_gpo.ask()
print(r)
#putting the ask() in a loop and updating the data will
#give you all you need for your autonomous experiment

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
fvGP training started with  100  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1.]  with old log likelihood:  -98.94089850406804
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  120
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= -163.469
differential_evolution step 2: f(x)= -163.469
differential_evolution step 3: f(x)= -163.469
differential_evolution step 4: f(x)= -163.719
differential_evolution step 5: f(x)= -163.719
differential_evolution step 6: f(x)= -163.719
differential_evolution step 7: f(x)= -164.002
differential_evolution step 8: f(x)= -164.002
differential_evolution step 9: f(x)= -164.002
differential_evolution step 10: f(x)= 